## Post Call Analytics (PCA) Using Amazon Bedrock
Amazon Bedrock을 사용한 통화 후 분석 사용 사례에 대한 이 교육에 오신 것을 환영합니다.

기업이 다양한 채널을 통해 고객과 계속 상호 작용함에 따라 이러한 상호 작용을 분석하여 고객 행동 및 선호도에 대한 인사이트를 얻는 것이 점점 더 중요해지고 있습니다.<BR>
통화 후 분석은 통화 종료 후 고객 상호 작용을 분석하는 방법 중 하나입니다.<BR>
대규모 언어 모델을 사용하면 보다 정확한 감정 분석을 가능하게 하고, 특정 고객의 요구와 선호도를 파악하며, 전반적인 고객 경험을 개선함으로써 통화 후 분석의 효과를 크게 높일 수 있습니다.<BR>

이 샘플 노트북에서는 통화 후 분석에 Bedrock을 사용할 때 얻을 수 있는 다양한 이점과 기업이 현대 시장에서 경쟁 우위를 확보할 수 있는 방법을 다음 주제를 통해 살펴봅니다.<BR>

- 베드락에서 LLM 모델 선택(타이탄 텍스트 및 앤트로닉 클로드)
- 하나의 모델로 여러 PCA 작업 처리
- 긴 통화 기록 처리

# 0. Auto Reload

In [7]:
%load_ext autoreload
%autoreload 2

# 1. Import packages

In [8]:
import os
import sys

module_path = "../../"
sys.path.append(os.path.abspath(module_path))

In [9]:
import json
import time
import boto3
import librosa
import langchain
import numpy as np
import IPython.display as ipd
from time import strftime
from termcolor import colored
from langchain import PromptTemplate
from langchain.llms.bedrock import Bedrock
import soundfile as sf
from utils import bedrock
from utils.s3 import s3_handler
from urllib.request import urlopen

sagemaker.config INFO - Not applying SDK defaults from location: /etc/xdg/sagemaker/config.yaml
sagemaker.config INFO - Not applying SDK defaults from location: /root/.config/sagemaker/config.yaml


# 2. Speech To Text (STT)

## 2.1. Run audio

In [10]:
ipd.Audio("./records/voice-examples.wav", autoplay=False)

## 2.2. Upload data to s3

In [11]:
s3 = s3_handler()

This is a S3 handler with [None] region.


In [18]:
prefix = "mx-40"
bucket_name = f'bedrock-training-{prefix}'
data_dir = "./records"

In [19]:
s3.create_bucket(bucket_name)
source_dir, target_bucket, target_dir = data_dir, bucket_name, "/records"
s3.upload_dir(source_dir, target_bucket, target_dir)
data_path_s3 =f's3://{bucket_name}/records/voice-examples.wav'

CREATE:[bedrock-training-mx-40] Bucket was created successfully
sagemaker.config INFO - Not applying SDK defaults from location: /etc/xdg/sagemaker/config.yaml
sagemaker.config INFO - Not applying SDK defaults from location: /root/.config/sagemaker/config.yaml
Upload:[./records] was uploaded to [s3://bedrock-training-mx-40/records]successfully


## 2.3. Transcribe

In [20]:
transcribe_client = boto3.client('transcribe')

In [21]:
create_date = strftime("%m%d-%H%M%s")
job_name = f'{prefix}-stt-job-{create_date}'
print (f's3 data path: {data_path_s3}')
print (f'job_name: {job_name}')

s3 data path: s3://bedrock-training-mx-40/records/voice-examples.wav
job_name: mx-40-stt-job-0920-03381695181127


### 2.3.1. Run Transcribe Job

In [22]:
transcribe_client.start_transcription_job(
    TranscriptionJobName=job_name,
    Media={'MediaFileUri': data_path_s3},
    MediaFormat='wav',
    Settings={
        'ShowSpeakerLabels': True,
        'MaxSpeakerLabels': 2,
    },
    LanguageCode='ko-KR'
)

{'TranscriptionJob': {'TranscriptionJobName': 'mx-40-stt-job-0920-03381695181127',
  'TranscriptionJobStatus': 'IN_PROGRESS',
  'LanguageCode': 'ko-KR',
  'MediaFormat': 'wav',
  'Media': {'MediaFileUri': 's3://bedrock-training-mx-40/records/voice-examples.wav'},
  'StartTime': datetime.datetime(2023, 9, 20, 3, 39, 12, 419000, tzinfo=tzlocal()),
  'CreationTime': datetime.datetime(2023, 9, 20, 3, 39, 12, 390000, tzinfo=tzlocal()),
  'Settings': {'ShowSpeakerLabels': True, 'MaxSpeakerLabels': 2}},
 'ResponseMetadata': {'RequestId': '7af51ffc-0908-41b1-9d87-3c9a5ebfaf60',
  'HTTPStatusCode': 200,
  'HTTPHeaders': {'x-amzn-requestid': '7af51ffc-0908-41b1-9d87-3c9a5ebfaf60',
   'content-type': 'application/x-amz-json-1.1',
   'content-length': '364',
   'date': 'Wed, 20 Sep 2023 03:39:11 GMT'},
  'RetryAttempts': 0}}

### 2.3.2. Check Job Status

In [23]:
while True:
    status = transcribe_client.get_transcription_job(TranscriptionJobName=job_name)
    if status['TranscriptionJob']['TranscriptionJobStatus'] in ['COMPLETED', 'FAILED']:
        break
    print("Not ready yet...")
    time.sleep(10)
print(status)

Not ready yet...
Not ready yet...
Not ready yet...
Not ready yet...
Not ready yet...
Not ready yet...
{'TranscriptionJob': {'TranscriptionJobName': 'mx-40-stt-job-0920-03381695181127', 'TranscriptionJobStatus': 'COMPLETED', 'LanguageCode': 'ko-KR', 'MediaSampleRateHertz': 8000, 'MediaFormat': 'wav', 'Media': {'MediaFileUri': 's3://bedrock-training-mx-40/records/voice-examples.wav'}, 'Transcript': {'TranscriptFileUri': 'https://s3.us-east-1.amazonaws.com/aws-transcribe-us-east-1-prod/738515539849/mx-40-stt-job-0920-03381695181127/f1a09865-125a-4169-9020-9cdccf891888/asrOutput.json?X-Amz-Security-Token=IQoJb3JpZ2luX2VjEOP%2F%2F%2F%2F%2F%2F%2F%2F%2F%2FwEaCXVzLWVhc3QtMSJIMEYCIQCVp3fuThmlicESDCHX6KGetkl9uiX%2BJFTt9oEWT16gVwIhANNcueA%2Bf7KIdp5Ta7eklwi4e5jEDmPMbpGxsaCG5PhoKroFCMz%2F%2F%2F%2F%2F%2F%2F%2F%2F%2FwEQBBoMMjc2NjU2NDMzMTUzIgylpCp9c91R%2Bdndu%2F0qjgXu0Iu%2Fwr1i4i28x9GcbmFvE01ElKm6m7W4wDg5%2FAjnbQH2nSufqSSPVZGMUswVhGB17dM9bKh9%2FmovKVQUwSBDIh9ht%2Fuu2f4IrOhHzUDP21gA9omSKRD9EpLQmDK9339v

In [26]:
response = urlopen(status['TranscriptionJob']['Transcript']['TranscriptFileUri'])
data = json.loads(response.read())

In [27]:
data

{'jobName': 'mx-40-stt-job-0920-03381695181127',
 'accountId': '738515539849',
 'results': {'transcripts': [{'transcript': '네, 고객님 중앙 교육의 이 진역 상담원입니다 안녕하세요? 결제 때문에 전화드렸어요 분당 사 때 중앙 교육 학습지 몇 년 했었고요 지금은 학습지 이용 안 하고 있거든요 그리고 저희 서 초로 이사도 했고요? 네, 고객님 근데 며칠 전에 갑자기 여기 학습지 결제 문자가 뜨더라고요 십팔만 원이 결제 됐는데 저희 지금 여기 학습지 이용을 안 하고 있어요 어떻게 된 건가요? 알아보겠습니다. 네, 빨리 알아봐 주세요 그때 분명히 선생님 하고도 잘 인사 했고 마치고 끝났는데 갑자기 결제 문자가 와서 놀랐거든요? 네, 알아본 결과 학습 종료가 안 된 걸로 나와 있습니다 학습 학습이 종료가 안 됐다고요? 저희 저번에 분명히 끝내고 인사까지 했는데요 죄송합니다 선생님하고 어떻게 해야해요? 길래 학습 종료가 안 돼요? 알아보고 처리해 드리겠습니다 처리해 주는 건 당연하고요 그것보다 저희 카드 번호도 분명히 개인 정보인데 해지하면 삭제해야 하는 거 아닌가요? 예전에 저희 학습 자 할 때도 결제 금액 이상해서 고객센터에 문의해 보니까 저희가 하지도 않은 과목을 등록 시켜서 그게 두 달 분이나 결제가 됐더라고요 그러셨군요 저희가 알았으니까 당정 이 이제 올랐으면 그렇게 남의 계좌에서 돈 계속 빼 나갔을 거 아니에요? 통제 같은 것도 안 해주고 죄송합니다 그때는 이제 애가 여기 선생님도 좋아하고 학습지도 마음에 들어서 그냥 넘겼어 거든요 남편은 이런 거 그냥 넘기면 안 된다고 했지만 애가 잘 하고 있는데 괜히 선생님 불편하게 만들어서 좋을 거 없으니까요. 근데 저희 분명히 그만 뒀는데 결제되는 건 좀 아니잖아요. 한 번 이해하고 넘어갔으면 좀 더 조심해야 조심해 줘야 하는 거 아닌가요? 그렇습니다. 그러면 이거 어떻게 처리해 줄 거예요? 저는 지금 당장 학습 종료 해 

### 2.3.3. Retrieve Text

In [ ]:
def spk_sperator(data):
    
    previos_spk = ""
    contents, contents_temp = [], []
    end_time = None
    
    for res in data["results"]["items"]:
        #print (res)
        speaker_label = res["speaker_label"]
        content = res["alternatives"][0]["content"]
        start_time = res.get("start_time", None)
        
        if previos_spk != speaker_label:
            
            contents_temp.append(f'<종료시간:{end_time}>')
            contents.append(" ".join(contents_temp))
            contents_temp = []
            
            contents_temp.append(f'{speaker_label}:<시작시간:{start_time}>')
            contents_temp.append(content)
        else:
            contents_temp.append(content)
            if content not in ["?", ",", "."]: end_time = res.get("end_time", None)
            
        previos_spk = speaker_label

    contents_temp.append(f'<종료시간:{end_time}>')
    contents.append(" ".join(contents_temp))
    
    return "\n".join(contents[1:])
    
if status['TranscriptionJob']['TranscriptionJobStatus'] == 'COMPLETED':
    response = urlopen(status['TranscriptionJob']['Transcript']['TranscriptFileUri'])
    data = json.loads(response.read())
    text = data['results']['transcripts'][0]['transcript']
    #print(text)
    
    text = spk_sperator(data)
    print (text)

# 3. Post Call Analytics

## 3.1. Choice of models in Bedrock
Choose FMs from Amazon, AI21 Labs and Anthropic to find the right FM for your use case.

**Select nternal-use: True(aws 직원), False (고객)** <BR>
**Select region: "us-east-1"(M1), "us-west-2"(M2)**

In [ ]:
is_internal_use = <internal-use> ## if 고객: False, aws직원: True

In [ ]:
bedrock_region = <your region> ## "us-east-1" or "us-west-2"

In [ ]:
if bedrock_region == "us-east-1":
    bedrock_config = {
        "region_name":bedrock_region,
        "endpoint_url": "https://bedrock.us-east-1.amazonaws.com" if is_internal_use else None
    }
elif bedrock_region == "us-west-2":
    bedrock_config = {
        "region_name":bedrock_region,
        "endpoint_url": "https://prod.us-west-2.frontend.bedrock.aws.dev" if is_internal_use else None
    }

In [ ]:
if is_internal_use:
    boto3_bedrock = boto3.client(
        service_name='bedrock',
        region_name=bedrock_config["region_name"],
        endpoint_url=bedrock_config["endpoint_url"]
    )
else:
    boto3_bedrock = boto3.client(
        service_name='bedrock',
        region_name=bedrock_config["region_name"]
    ) 

In [ ]:
bedrock_models = {
    "Claude" : "anthropic.claude-v1",
    "TitanText": "amazon.titan-tg1-large", 
    "Claude-instant":"anthropic.claude-instant-v1",
    "Claude-V2" : "anthropic.claude-v2",
}

max_tokens = {
    "Claude" : 12000,
    "TitanText": 4096,
    "Claude-instant": 9000,
    "Claude-V2" : 12000,
}

max_tokens = {"Claude" : 120, "TitanText": 130, "Claude-instant": 120, "Claude-V2" : 120}


In [ ]:
# Choose one of the bedrock model
model = "Claude-V2" # "Claude", "TitanText", "Claude-instant"
if model in ["Claude", "Claude-instant", "Claude-V2"]:
    llm = Bedrock(
        model_id=bedrock_models[model],
        client=boto3_bedrock,
        model_kwargs={
            "max_tokens_to_sample":512,
            "stop_sequences":["\n\nhuman", "\n\n인간", "\n\n상담원", "\n\n"],
            "temperature":0,
            "top_p":0.9
        },
    )
elif model == "TitanText":
    llm = Bedrock(
        model_id=bedrock_models[model],
        client=bedrock,
        model_kwargs={
            "maxTokenCount":4096,
            "stopSequences":[],
            "temperature":0,
            "topP":0.9
        },
    )

## 3.2. Prompt Template
이 노트북에서는 네 가지 분석(**요약, 감성, 의도, 해결**)을 수행하게 되며, 각 분석에 대한 템플릿이 필요합니다.

In [ ]:
summary_template_ko = """
아래의 통화 기록을 분석하세요. 전체 문장으로 대화에 대한 자세한 요약을 제공하세요.

통화: "{transcript}"

요약:"""

question_template_ko = """

아래의 통화 기록을 바탕으로 질문에 답하세요.
"<시작시간>" 이어지는 문장의 시작시간을 나타내고 "<종료시간>"은 앞 문장의 종료시간을 나타냅니다.

통화: "{transcript}"

질문: "{question}"

응답: """

question_time_template_ko = """

아래의 통화 기록을 바탕으로 질문에 답하세요.
"<시작시간>" 이어지는 문장의 시작시간을 나타내고 "<종료시간>"은 앞 문장의 종료시간을 나타냅니다.

통화: "{transcript}"

질문: "{question} 답변과 함께 답변을 위해 참조한 대화의 시작 및 종료시간을 아래 형태로 알려주세요. \n답변:\n시작시간:\n종료시간:"

응답: """


## 3.3. Generate Analysis

In [ ]:
def analysis(llm, transcript, params, question=None, template="", max_tokens=50):
 
    if question is None:
        prompt = PromptTemplate(template=template, input_variables=["transcript"])
        analysis_prompt = prompt.format(transcript=transcript)
    else:
        prompt = PromptTemplate(template=template, input_variables=["transcript", "question"])
        analysis_prompt = prompt.format(
            transcript=transcript,
            question=question
        )
        
    llm.model_kwargs = params
        
    print (colored(analysis_prompt, 'green'))
    response = llm(analysis_prompt)
    
    return response

def get_clues(res):
    
    def _extract_time(res):
        for item in res.split("\n"):
            if "시작시간:" in item:
                start_time = item.replace("시작시간:", "").strip()
            elif "종료시간:" in item:
                end_time = item.replace("종료시간:", "").strip()

        return start_time, end_time
    
    def _trim_audio_data(audio_file, save_file, start, end):
        sr = 96000
        y, sr = librosa.load(audio_file, sr=sr)
        ny = y[sr*(int(float(start))-3):sr*(int(float(end))+3)]
        sf.write(save_file, ny, 96000)
    
    start_time, end_time = _extract_time(res)
    
    print (start_time, end_time)
    _trim_audio_data("./records/voice-examples.wav", "./records/clue/clue.wav", start_time, end_time)

In [ ]:
PARAMS = {
    "max_tokens_to_sample":512,
    "stop_sequences":["\n\nhuman", "\n\n인간", "\n\n상담사", "\n\n\n", "\n\n질문"],
    "temperature":0,
    "top_p":0.9
}

### 3.3.1. Summary

In [ ]:
%%time

res = analysis(
    llm=llm,
    transcript=text,
    params=PARAMS,
    template=summary_template_ko
)

print (res)

### 3.3.2. Question and Answer

In [ ]:
%%time
question = "고객의 감정은 어떤가요?"

res = analysis(
    llm=llm,
    transcript=text,
    params=PARAMS,
    question=question,
    template=question_template_ko
)

print (res)

In [ ]:
%%time
question = "문제에 대한 개선을 위해서 어떤 방법이 있을까요?"

res = analysis(
    llm=llm,
    transcript=text,
    params=PARAMS,
    question=question,
    template=question_template_ko
)

print (res)

In [ ]:
%%time
question = "학습지는 언제 종료되나요?"

res = analysis(
    llm=llm,
    transcript=text,
    params=PARAMS,
    question=question,
    template=question_time_template_ko
)

print (res)
get_clues(res)
ipd.Audio("./records/clue/clue.wav", autoplay=False)

In [ ]:
%%time
question = "학습지는 언제 종료되고 환불은 언제 가능한가요?"

res = analysis(
    llm=llm,
    transcript=text,
    params=PARAMS,
    question=question,
    template=question_time_template_ko
)

print (res)
get_clues(res)
ipd.Audio("./records/clue/clue.wav", autoplay=False)

In [ ]:
%%time
question = "결제된 금액은 얼마인가요?"

res = analysis(
    llm=llm,
    transcript=text,
    params=PARAMS,
    question=question,
    template=question_time_template_ko
)

print (res)
get_clues(res)
ipd.Audio("./records/clue/clue.wav", autoplay=False)

In [ ]:
%%time
question = "상담원의 이름은 무엇인가요?"

res = analysis(
    llm=llm,
    transcript=text,
    params=PARAMS,
    question=question,
    template=question_time_template_ko
)

print (res)
get_clues(res)
ipd.Audio("./records/clue/clue.wav", autoplay=False)

## 3.4. Handling long call transcripts
LLM의 인풋 토큰 한도를 초과하는 긴 문서를 처리하는 방법을 다룹니다. 

* Map Reduce
![nn](../../imgs/map_reduce.png)
출처: https://brain.d.foundation/Engineering/AI/Workaround+with+OpenAI's+token+limit+with+Langchain

* Refine
![nn](../../imgs/refine.png)
출처: https://brain.d.foundation/Engineering/AI/Workaround+with+OpenAI's+token+limit+with+Langchain

In [ ]:
from langchain.chains.summarize import load_summarize_chain
from langchain.text_splitter import RecursiveCharacterTextSplitter

* prompting to divide and conquer

In [ ]:
stuff_prompt_template = """
다음 통화를 간단하게 요약해 주세요.

통화: {text}

요약:
"""

chuck_prompt_template = """
다음 통화를 간단하게 요약해 주세요.

통화: {text}

요약:
"""

chunk_prompt = PromptTemplate(
    template=chuck_prompt_template,
    input_variables=["text"]
)

combine_prompt_template = """
다음 통화를 간단하게 요약해 주세요.

통화: {text}

요약:
"""

combine_prompt = PromptTemplate(
    template=combine_prompt_template,
    input_variables=["text"]
)

* summarize chain

In [ ]:
def summary_chain_init(chain_type, llm):


    combine_prompt = PromptTemplate(
        template=combine_prompt_template,
        input_variables=["text"]
    )

    if chain_type == "STUFF":
        chain = load_summarize_chain(
            llm,
            chain_type="stuff",
            verbose=True
        )
        
    elif chain_type == "MAP_REDUCE":
        chain = load_summarize_chain(
            llm,
            chain_type="map_reduce",
            map_prompt=chunk_prompt,
            combine_prompt=combine_prompt,
            return_intermediate_steps=True,
            verbose=True
        )
    elif chain_type == "REFINE":
        chain = load_summarize_chain(
            llm,
            chain_type="refine",
            question_prompt=chunk_prompt,
            refine_prompt=combine_prompt,
            return_intermediate_steps=True,
            verbose=True
        )
        
    return chain

In [ ]:
def long_call_analysis(llm, transcript, params, chain_type="MAP_REDUCE", max_tokens=50):

    
    llm.model_kwargs = params
    num_tokens = llm.get_num_tokens(transcript) #raise warnning
    
    print (num_tokens, max_tokens)

    if num_tokens > max_tokens:
        text_splitter = RecursiveCharacterTextSplitter(
            #separators=["\n\n\n"],
            chunk_size=500,
            chunk_overlap=100
        )
        docs = text_splitter.create_documents([transcript])
        num_docs = len(docs)
        num_tokens_first_doc = llm.get_num_tokens(docs[0].page_content)

        print(f"Now we have {num_docs} documents and the first one has {num_tokens_first_doc} tokens")

        
        summary_chain = summary_chain_init(
            chain_type=chain_type, 
            llm=llm
        )
        response = summary_chain(
            {"input_documents": docs}
        )
        
        print ("Intermediate_steps: \n")
        for idx, step in enumerate(response["intermediate_steps"]):
            print (colored(f'step {idx}: \n', "green"))
            print (colored(f'{step}\n', "green"))
        
        return response["output_text"]
    
    else:
        
        prompt = PromptTemplate(template=stuff_prompt_template, input_variables=["text"])
        analysis_prompt = prompt.format(text=transcript)
        print (colored(analysis_prompt, 'green'))
        
        response = llm(analysis_prompt)
        
        return response
        

In [ ]:
PARAMS = {
    "max_tokens_to_sample":512,
    "stop_sequences":["\n\nhuman", "\n\n인간", "\n\n상담사", "\n\n\n", "\n\n질문", "\n\nspk_0", "\n\n통화"],
    "temperature":0,
    "top_p":0.9
}

In [ ]:
%%time

res = long_call_analysis(
    llm=llm,
    transcript=text,
    params=PARAMS,
    chain_type="REFINE" # REFINE, MAP_REDUCE
)

print ("Results: \n")
print (res)